# NB #2:  Arbitrage 

### Pool address: 0x8b6e6E7B5b3801FEd2CaFD4b22b8A16c2F2Db21a  -- 80% WETH - 20% DAI 

The Balancer Pool cadCAD model provides a core infrastructure for simulating Balancer Pools in the **Token Engineering Design and Verification process**.

It allows to simulate Balancer Pool transactions and verify new designs and application cases.  
In this notebook we plug **historical on-chain data** to a cadCAD model, and analyse **Pool Power** and **Pool Characteristics**.

For more information check out the [Balancer Simulations documentation](https://token-engineering-balancer.gitbook.io/balancer-simulations/).

# A. System Context

### A1.1 System Specification
System specification details are available in the Balancer Simulations documentation:
- [Differential Specification](https://token-engineering-balancer.gitbook.io/balancer-simulations/balancer-simulations/v10nboverview)
- [Mathematical Specification](https://token-engineering-balancer.gitbook.io/balancer-simulations/additional-code-and-instructions/balancer-the-python-edition/balancer_math.py)
- [Model Architecture](https://token-engineering-balancer.gitbook.io/balancer-simulations/balancer-simulations/v10nboverview)
- [Naming Convention](https://token-engineering-balancer.gitbook.io/balancer-simulations/additional-code-and-instructions/naming-convention)

# B. cadCAD Simulations

### B1.1 Dependencies

In [1]:
import pandas as pd 
from cadCAD.configuration.utils import config_sim
from model.models import Token, Pool

### B1.2 Initialize Pool


In this section you specify the Balancer Pool to be analyzed and run scripts to produce the'genesis_state', based on on-chain data. 

More information here: [Balancer Simulations documentation](https://token-engineering-balancer.gitbook.io/balancer-simulations/additional-code-and-instructions/onchaintransactions).  

In [2]:
import pprint
pp = pprint.PrettyPrinter(indent=4)

from decimal import Decimal

# No spot_price_reference means all pairs are calculated.
parameters = {
    'decoding_type': ['SIMPLIFIED'],
    'external_currency': ['USD'],
    'max_arb_liquidity': [100000],
    'min_arb_liquidity': [10],
    'arb_liquidity_granularity': [50],
    'weight_changing': [False]
    
}


#### Create your pool

Create your genesis states using our Token and Pool classes. Pool will check for token weight integrity

Token prices could come from initial state files

// TODO document
Learn more how to create this variables [documentation](https://token-engineering-balancer.gitbook.io/balancer-simulations/v/master/todo).


In [3]:
from model.genesis_states import generate_initial_state


tokens = {
    'DAI': Token(denorm_weight=10, balance=Decimal('10000000'), bound=True),
    'WETH': Token(denorm_weight=40, balance=Decimal('67738.636173102396002749'), bound=True)
}
generated_fees = {
    'WETH': Decimal('0'),
    'DAI': Decimal('0')
}    
initial_values = {
    'pool': Pool(tokens=tokens,
               generated_fees=generated_fees,
               shares=Decimal('100'),
               swap_fee=Decimal('0.0025')),
    
}
initial_values['spot_prices'] = initial_values['pool'].spot_prices(ref_token=None)


print(initial_values)


{'pool': <Pool tokens: {'DAI': <Token weight: 0.2 (calculated), denorm_weight: 10, balance: 10000000, bound: True>, 'WETH': <Token weight: 0.8 (calculated), denorm_weight: 40, balance: 67738.636173102396002749, bound: True>} generated_fees: {'WETH': Decimal('0'), 'DAI': Decimal('0')} shares: 100 swap_fee: 0.0025 >, 'spot_prices': {'DAI': {'WETH': Decimal('591.9849127769919849127838632')}, 'WETH': {'DAI': Decimal('0.001697710179777002406083934838')}}}


#### State Variables and Initial Values

In [4]:
print('## State Variables')
print('# Pool')
initial_values['gas_cost'] = Decimal('30')
initial_values['token_prices'] = {
        'WETH': Decimal('596.1937868299183'),
        'DAI': Decimal('1.0037648993426744')
    }
initial_values['change_datetime'] = '2020-12-07T13:34:14+00:00'
initial_values['action_type'] = 'pool_creation'

pp.pprint(initial_values)


## State Variables
# Pool
{   'action_type': 'pool_creation',
    'change_datetime': '2020-12-07T13:34:14+00:00',
    'gas_cost': Decimal('30'),
    'pool': <Pool tokens: {'DAI': <Token weight: 0.2 (calculated), denorm_weight: 10, balance: 10000000, bound: True>, 'WETH': <Token weight: 0.8 (calculated), denorm_weight: 40, balance: 67738.636173102396002749, bound: True>} generated_fees: {'WETH': Decimal('0'), 'DAI': Decimal('0')} shares: 100 swap_fee: 0.0025 >,
    'spot_prices': {   'DAI': {   'WETH': Decimal('591.9849127769919849127838632')},
                       'WETH': {   'DAI': Decimal('0.001697710179777002406083934838')}},
    'token_prices': {   'DAI': Decimal('1.0037648993426744'),
                        'WETH': Decimal('596.1937868299183')}}


#### External USD Token Prices

In [5]:
print('# External token prices, initial state')
token_prices = initial_values['token_prices']
pp.pprint(token_prices)

print('# Action Type')
action_type = initial_values['action_type']
pp.pprint(action_type)


# External token prices, initial state
{'DAI': Decimal('1.0037648993426744'), 'WETH': Decimal('596.1937868299183')}
# Action Type
'pool_creation'


### B1.3 State Update Functions & Policies

Balancer Simulations replicate Balancer Pool Transactions in state update functions.  
For a detailed description, please visit the [Balancer Simulations documentation](https://token-engineering-balancer.gitbook.io/balancer-simulations/additional-code-and-instructions/balancer-the-python-edition).

### B1.4 Partial State Update Blocks

Partial State Update Blocks combine the following steps:  
1. **Initialize pool**, generate genesis state
2. Compute subsequent **actions in discrete timesteps**, store datetime and update the pool state variables
3. Update external **USD prices in discrete timesteps**, and store datetime  

For more information please visit the [Balancer Simulations documentation/Model Overview](https://token-engineering-balancer.gitbook.io/balancer-simulations/v/master/balancer-simulations/v10nboverview).  

To inject historical on-chain transactions to the model, reference the **actions.json of your pool below**.

In [6]:
from model.partial_state_update_block import generate_partial_state_update_blocks

result = generate_partial_state_update_blocks(path_to_action_json='data/0x8b6e6e7b5b3801fed2cafd4b22b8a16c2f2db21a-actions-prices-only.json',
                                              add_arbitrage=True)
partial_state_update_blocks = result['partial_state_update_blocks']
pp.pprint(partial_state_update_blocks)

[   {   'policies': {   'external_signals': <function ActionDecoder.p_action_decoder at 0x7f98ca197820>},
        'variables': {   'action_type': <function s_update_action_type at 0x7f98ca1978b0>,
                         'change_datetime': <function s_update_change_datetime at 0x7f98ca18bd30>,
                         'pool': <function s_update_pool at 0x7f98ca197b80>,
                         'spot_prices': <function s_update_spot_prices at 0x7f98ca197dc0>,
                         'token_prices': <function s_update_external_price_feeds at 0x7f98ca1a24c0>}},
    {   'policies': {'arbitrage': <function p_arbitrageur at 0x7f98ca18bb80>},
        'variables': {   'change_datetime': <function s_update_change_datetime at 0x7f98ca18bd30>,
                         'pool': <function s_update_pool at 0x7f98ca197b80>,
                         'spot_prices': <function s_update_spot_prices at 0x7f98ca197dc0>}}]


### B1.5 Configuration

[cadCAD simulations](https://github.com/cadCAD-org/cadCAD/blob/master/documentation/README.md) support Monte Carlo runs, and parameter sweeps which are not applied in this notebook and can be ignored here.  
Timesteps 'T' are defined by your pool's .json file, no need to make edits here.

In [7]:
steps_number = result['steps_number']
print('# Steps ', steps_number)
sim_config = config_sim(
    {
        'N': 1,  # number of monte carlo runs
        'T': range(steps_number - 1),  # number of timesteps
        'M': parameters,  # simulation parameters
    }
)

# Steps  1936


### B1.6 Execution

In [8]:
from model.sim_runner import *
from ipdb import launch_ipdb_on_exception


with launch_ipdb_on_exception():
    df = run(initial_values, partial_state_update_blocks, sim_config)


                  ___________    ____
  ________ __ ___/ / ____/   |  / __ \
 / ___/ __` / __  / /   / /| | / / / /
/ /__/ /_/ / /_/ / /___/ ___ |/ /_/ /
\___/\__,_/\__,_/\____/_/  |_/_____/
by cadCAD

Execution Mode: single_proc
Configuration Count: 1
Dimensions of the first simulation: (Timesteps, Params, Runs, Vars) = (1935, 6, 1, 6)
Execution Method: single_proc_exec
Execution Mode: single_threaded
Timestep 1 <Pool tokens: {'DAI': <Token weight: 0.2 (calculated), denorm_weight: 10, balance: 10000000, bound: True>, 'WETH': <Token weight: 0.8 (calculated), denorm_weight: 40, balance: 67738.636173102396002749, bound: True>} generated_fees: {'WETH': Decimal('0'), 'DAI': Decimal('0')} shares: 100 swap_fee: 0.0025 >
1 DAI (token_in) is ~1.00 USD on external markets, can come out via {'WETH': Decimal('1.005957910056688226468389560')} USD (token_out)
1 WETH (token_in) is ~595.51 USD on external markets, can come out via {'DAI': Decimal('591.4880508656502958679232667')} USD (token_out)
cal

most_profitable_trade: 100432.379 DAI -> 222.130 WETH, profit 131030.078 USD
Timestep 12 <Pool tokens: {'DAI': <Token weight: 0.2 (calculated), denorm_weight: 10, balance: 8112766.910114268869707492770, bound: True>, 'WETH': <Token weight: 0.8 (calculated), denorm_weight: 40, balance: 71394.83352803852097669913926, bound: True>} generated_fees: {'WETH': Decimal('0'), 'DAI': Decimal('0')} shares: 100 swap_fee: 0.0025 >
1 DAI (token_in) is ~1.01 USD on external markets, can come out via {'WETH': Decimal('1.294723950819687205873738110')} USD (token_out)
1 WETH (token_in) is ~589.97 USD on external markets, can come out via {'DAI': Decimal('455.7354212688454177823565903')} USD (token_out)
calculating optimal trade size
most_profitable_trade: 100476.367 DAI -> 218.816 WETH, profit 129063.922 USD
Timestep 13 <Pool tokens: {'DAI': <Token weight: 0.2 (calculated), denorm_weight: 10, balance: 8213243.277080925325366783029, bound: True>, 'WETH': <Token weight: 0.8 (calculated), denorm_weight: 40

most_profitable_trade: 100876.500 DAI -> 190.033 WETH, profit 109474.121 USD
Timestep 23 <Pool tokens: {'DAI': <Token weight: 0.2 (calculated), denorm_weight: 10, balance: 9218007.546369506134551945962, bound: True>, 'WETH': <Token weight: 0.8 (calculated), denorm_weight: 40, balance: 69156.69614136899198972941054, bound: True>} generated_fees: {'WETH': Decimal('0'), 'DAI': Decimal('0')} shares: 100 swap_fee: 0.0025 >
1 DAI (token_in) is ~1.01 USD on external markets, can come out via {'WETH': Decimal('1.077909480169404877134532101')} USD (token_out)
1 WETH (token_in) is ~576.15 USD on external markets, can come out via {'DAI': Decimal('535.3962547677476102389864565')} USD (token_out)
calculating optimal trade size
most_profitable_trade: 100629.626 DAI -> 186.997 WETH, profit 107707.377 USD
Timestep 24 <Pool tokens: {'DAI': <Token weight: 0.2 (calculated), denorm_weight: 10, balance: 9318637.172376818868535968619, bound: True>, 'WETH': <Token weight: 0.8 (calculated), denorm_weight: 40

most_profitable_trade: 99650.989 DAI -> 243.037 WETH, profit 134250.291 USD
Timestep 34 <Pool tokens: {'DAI': <Token weight: 0.2 (calculated), denorm_weight: 10, balance: 7507945.929040554757347860718, bound: True>, 'WETH': <Token weight: 0.8 (calculated), denorm_weight: 40, balance: 72816.46417395338695369811680, bound: True>} generated_fees: {'WETH': Decimal('0'), 'DAI': Decimal('0')} shares: 100 swap_fee: 0.0025 >
1 DAI (token_in) is ~1.00 USD on external markets, can come out via {'WETH': Decimal('1.338645590952376113382038858')} USD (token_out)
1 WETH (token_in) is ~553.48 USD on external markets, can come out via {'DAI': Decimal('413.3407773133959114663903376')} USD (token_out)
calculating optimal trade size
most_profitable_trade: 100431.524 DAI -> 240.897 WETH, profit 133302.131 USD
Timestep 35 <Pool tokens: {'DAI': <Token weight: 0.2 (calculated), denorm_weight: 10, balance: 7608377.453280783290787849896, bound: True>, 'WETH': <Token weight: 0.8 (calculated), denorm_weight: 40,

most_profitable_trade: 100535.643 DAI -> 206.301 WETH, profit 113269.076 USD
Timestep 45 <Pool tokens: {'DAI': <Token weight: 0.2 (calculated), denorm_weight: 10, balance: 8614017.428797208995001779644, bound: True>, 'WETH': <Token weight: 0.8 (calculated), denorm_weight: 40, balance: 70363.18751919762105018650559, bound: True>} generated_fees: {'WETH': Decimal('0'), 'DAI': Decimal('0')} shares: 100 swap_fee: 0.0025 >
1 DAI (token_in) is ~1.01 USD on external markets, can come out via {'WETH': Decimal('1.146597826567410044411722390')} USD (token_out)
1 WETH (token_in) is ~562.88 USD on external markets, can come out via {'DAI': Decimal('491.1160628890559541484470867')} USD (token_out)
calculating optimal trade size
most_profitable_trade: 100502.589 DAI -> 203.248 WETH, profit 114375.088 USD
Timestep 46 <Pool tokens: {'DAI': <Token weight: 0.2 (calculated), denorm_weight: 10, balance: 8714520.017808907630143691139, bound: True>, 'WETH': <Token weight: 0.8 (calculated), denorm_weight: 40

...

most_profitable_trade: 100486.667 DAI -> 77.782 WETH, profit 126441.158 USD
Timestep 1882 <Pool tokens: {'DAI': <Token weight: 0.2 (calculated), denorm_weight: 10, balance: 19010057.70906091527949962780, bound: True>, 'WETH': <Token weight: 0.8 (calculated), denorm_weight: 40, balance: 58811.33077993675254288300285, bound: True>} generated_fees: {'WETH': Decimal('0'), 'DAI': Decimal('0')} shares: 100 swap_fee: 0.0025 >
1 DAI (token_in) is ~1.00 USD on external markets, can come out via {'WETH': Decimal('1.258254767327153952567046217')} USD (token_out)
1 WETH (token_in) is ~1630.94 USD on external markets, can come out via {'DAI': Decimal('1288.665524789222674990279953')} USD (token_out)
calculating optimal trade size
most_profitable_trade: 99878.298 DAI -> 76.804 WETH, profit 125232.313 USD
Timestep 1883 <Pool tokens: {'DAI': <Token weight: 0.2 (calculated), denorm_weight: 10, balance: 19109936.00713431986046527852, bound: True>, 'WETH': <Token weight: 0.8 (calculated), denorm_weight: 

most_profitable_trade: 100324.397 DAI -> 72.373 WETH, profit 120600.511 USD
Timestep 1893 <Pool tokens: {'DAI': <Token weight: 0.2 (calculated), denorm_weight: 10, balance: 20109988.33666773384499778687, bound: True>, 'WETH': <Token weight: 0.8 (calculated), denorm_weight: 40, balance: 57992.14060327510244342585199, bound: True>} generated_fees: {'WETH': Decimal('0'), 'DAI': Decimal('0')} shares: 100 swap_fee: 0.0025 >
1 DAI (token_in) is ~1.00 USD on external markets, can come out via {'WETH': Decimal('1.189716960029211438185024182')} USD (token_out)
1 WETH (token_in) is ~1654.37 USD on external markets, can come out via {'DAI': Decimal('1382.556259556512488361832024')} USD (token_out)
calculating optimal trade size
most_profitable_trade: 99883.439 DAI -> 71.608 WETH, profit 118436.413 USD
Timestep 1894 <Pool tokens: {'DAI': <Token weight: 0.2 (calculated), denorm_weight: 10, balance: 20209871.77539856502822098904, bound: True>, 'WETH': <Token weight: 0.8 (calculated), denorm_weight: 

most_profitable_trade: 100229.344 DAI -> 67.630 WETH, profit 108985.681 USD
Timestep 1904 <Pool tokens: {'DAI': <Token weight: 0.2 (calculated), denorm_weight: 10, balance: 21212293.42556290941612425925, bound: True>, 'WETH': <Token weight: 0.8 (calculated), denorm_weight: 40, balance: 57225.50550931545839559602182, bound: True>} generated_fees: {'WETH': Decimal('0'), 'DAI': Decimal('0')} shares: 100 swap_fee: 0.0025 >
1 DAI (token_in) is ~1.00 USD on external markets, can come out via {'WETH': Decimal('1.084443571743662218292036017')} USD (token_out)
1 WETH (token_in) is ~1611.95 USD on external markets, can come out via {'DAI': Decimal('1476.579624779210088494541986')} USD (token_out)
calculating optimal trade size
most_profitable_trade: 99795.793 DAI -> 66.942 WETH, profit 107876.598 USD
Timestep 1905 <Pool tokens: {'DAI': <Token weight: 0.2 (calculated), denorm_weight: 10, balance: 21312089.21887108453763856218, bound: True>, 'WETH': <Token weight: 0.8 (calculated), denorm_weight: 

most_profitable_trade: 99994.478 DAI -> 63.323 WETH, profit 103335.022 USD
Timestep 1915 <Pool tokens: {'DAI': <Token weight: 0.2 (calculated), denorm_weight: 10, balance: 22314596.84483760852002228902, bound: True>, 'WETH': <Token weight: 0.8 (calculated), denorm_weight: 40, balance: 56507.09777925763411345345916, bound: True>} generated_fees: {'WETH': Decimal('0'), 'DAI': Decimal('0')} shares: 100 swap_fee: 0.0025 >
1 DAI (token_in) is ~1.00 USD on external markets, can come out via {'WETH': Decimal('1.032208899762637094026629300')} USD (token_out)
1 WETH (token_in) is ~1634.56 USD on external markets, can come out via {'DAI': Decimal('1575.437363728489899194533801')} USD (token_out)
calculating optimal trade size
most_profitable_trade: 99946.698 DAI -> 62.940 WETH, profit 102848.756 USD
Timestep 1916 <Pool tokens: {'DAI': <Token weight: 0.2 (calculated), denorm_weight: 10, balance: 22414543.54278539718689819026, bound: True>, 'WETH': <Token weight: 0.8 (calculated), denorm_weight: 4

most_profitable_trade: 100150.661 DAI -> 197.318 WETH, profit 293358.340 USD
Timestep 1926 <Pool tokens: {'DAI': <Token weight: 0.2 (calculated), denorm_weight: 10, balance: 9034480.303352051782859654966, bound: True>, 'WETH': <Token weight: 0.8 (calculated), denorm_weight: 40, balance: 70881.75438814902348772067521, bound: True>} generated_fees: {'WETH': Decimal('0'), 'DAI': Decimal('0')} shares: 100 swap_fee: 0.0025 >
1 DAI (token_in) is ~1.00 USD on external markets, can come out via {'WETH': Decimal('2.903089855774101882344886823')} USD (token_out)
1 WETH (token_in) is ~1483.80 USD on external markets, can come out via {'DAI': Decimal('509.3758531898723070941773006')} USD (token_out)
calculating optimal trade size
most_profitable_trade: 100120.495 DAI -> 194.545 WETH, profit 288637.144 USD
Timestep 1927 <Pool tokens: {'DAI': <Token weight: 0.2 (calculated), denorm_weight: 10, balance: 9134600.798346063011923712000, bound: True>, 'WETH': <Token weight: 0.8 (calculated), denorm_weigh

### B1.7 Simulation Output Preparation

Post-processing (utils.py) splits up state variable dictionaries, and adds metrics to the data frame, such as 
- `token_total_value` (TVL)
- `generated_fees_(tokensymbol)` (fee collected per transaction)
- `token_k_values`  (token value in USD)  
based on  
- `token_k_balances`
- `token_k_price`  (external price feed)

In [9]:
from model.parts.utils import post_processing
p_df = post_processing(df, include_spot_prices=True)
p_df = p_df[p_df['substep'] == 2]
p_df.tail()

pool  \
3862  <Pool tokens: {'DAI': <Token weight: 0.2 (calc...   
3864  <Pool tokens: {'DAI': <Token weight: 0.2 (calc...   
3866  <Pool tokens: {'DAI': <Token weight: 0.2 (calc...   
3868  <Pool tokens: {'DAI': <Token weight: 0.2 (calc...   
3870  <Pool tokens: {'DAI': <Token weight: 0.2 (calc...   

                                            spot_prices gas_cost  \
3862  {'DAI': {'WETH': 554.0585634787382970760444290...       30   
3864  {'DAI': {'WETH': 561.3617761079638020769719213...       30   
3866  {'DAI': {'WETH': 568.6197464541923092353072212...       30   
3868  {'DAI': {'WETH': 575.9277233453301345526641709...       30   
3870  {'DAI': {'WETH': 583.2542567443275305290843028...       30   

                                           token_prices  \
3862  {'DAI': 1.010645244497032, 'WETH': 1424.668024...   
3864  {'DAI': 1.015823838663806, 'WETH': 1445.515630...   
3866  {'DAI': 1.006920828125983, 'WETH': 1459.901131...   
3868  {'DAI': 1.011269757254227, 'WETH': 1484.140462...   
3870  {'DAI': 1.011269757254227, 'WETH': 1460.303461...   

               change_datetime            action_type  simulation  subset  \
3862 2021-02-26 08:00:15+00:00  external_price_update           0       0   
3864 2021-02-26 09:00:15+00:00  external_price_update           0       0   
3866 2021-02-26 10:00:15+00:00  external_price_update           0       0   
3868 2021-02-26 11:00:15+00:00  external_price_update           0       0   
3870 2021-02-26 12:00:15+00:00  external_price_update           0       0   

      run  substep  ...  pool_shares token_dai_price  token_weth_price  \
3862    1        2  ...          100        1.010645       1424.668024   
3864    1        2  ...          100        1.015824        1445.51563   
3866    1        2  ...          100        1.006921       1459.901132   
3868    1        2  ...          100         1.01127       1484.140462   
3870    1        2  ...          100         1.01127       1460.303462   

      token_spot_price_dai_weth  token_spot_price_weth_dai  token_dai_value  \
3862                 554.058563                   0.001814     9.739749e+06   
3864                 561.361776                   0.001790     9.892804e+06   
3866                 568.619746                   0.001767     9.907449e+06   
3868                 575.927723                   0.001745     1.005247e+07   
3870                 583.254257                   0.001723     1.015469e+07   

      token_weth_value           tvl      invariant  total_token_balances  
3862      9.936973e+07  1.091095e+08  186905.529323          9.706908e+06  
3864      1.005606e+08  1.104535e+08  186906.503735          9.808268e+06  
3866      1.013013e+08  1.112088e+08  186907.459731          9.908742e+06  
3868      1.027211e+08  1.127736e+08  186908.410097          1.000965e+07  
3870      1.008166e+08  1.109713e+08  186909.350900          1.011056e+07  

[5 rows x 32 columns]

# C. Simulation Outcome & Pool Exploration

The plots below offer some keys metrics for pool analysis.

**a) Pool Power:**  
- C1.1 TVL (Total Value Locked) vs. Pool Growth (token balances in the pool, over time)
- C1.2 Token Balances (individual token balances, over time)

**b) Pool Characteristics:**  
- C1.3 Sources of Pool Growth (BPT, Fees)
- C1.4 Token Ratio
- C1.5 Action Types

In [10]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

In [11]:
print("Observation Time")
print(f"Start: {p_df['change_datetime'].min()}")
print(f"End: {p_df['change_datetime'].max()}")
print(f"Total Observation Period: {p_df['change_datetime'].max() - p_df['change_datetime'].min()}")
print("\n")
print(f"Total No. of Timesteps (incl. Price Updates): {(p_df.iloc[-1]['timestep'])}")
print(f"Total No. of Transactions: {len(p_df[p_df.action_type != 'external_price_update'])}")

Observation Time
Start: 2020-12-07 16:00:15+00:00
End: 2021-02-26 12:00:15+00:00
Total Observation Period: 80 days 20:00:00


Total No. of Timesteps (incl. Price Updates): 1935
Total No. of Transactions: 0


### Balances

In [12]:
fig = make_subplots(specs=[[{'secondary_y': True}]])
fig.add_trace(go.Scatter(x=p_df.timestep, y=p_df.token_dai_balance, line=dict(color='#f36315'), name="Balance DAI"), secondary_y=False)
fig.add_trace(go.Scatter(x=p_df.timestep, y=p_df.token_weth_balance, line=dict(color='red'), name="Balance WETH"), secondary_y=False)

fig.update_layout(title_text='<b>Balances Prices</b>')
fig.update_xaxes(title_text='timestep')

fig.show()  

In [13]:
### Prices

In [14]:
fig = make_subplots(specs=[[{'secondary_y': True}]])
fig.add_trace(go.Scatter(x=p_df.timestep, y=p_df.token_dai_price, line=dict(color='blue'), name="External Price DAI"), secondary_y=False)
fig.add_trace(go.Scatter(x=p_df.timestep, y=p_df.token_weth_price, line=dict(color='green'), name="External Price WETH"), secondary_y=False)
fig.add_trace(go.Scatter(x=p_df.timestep, y=p_df.token_spot_price_weth_dai, line=dict(color='red'), name="Spot Price WETH DAI"), secondary_y=True)

fig.update_layout(title_text='<b>Balances Prices</b>')
fig.update_xaxes(title_text='timestep')

fig.show()  

### C1.1 TVL & Pool Size Growth

In [15]:
#TVL vs. Pool Size Growth
fig = make_subplots(specs=[[{'secondary_y': True}]])
fig.add_trace(go.Scatter(x=p_df.timestep, y=p_df.tvl, line=dict(color='#f36315'), name="TVL total_token_value"), secondary_y=False)
fig.add_trace(go.Scatter(x=p_df.timestep,y=p_df.total_token_balances, line=dict(color='#2C1839'), name="total_token_balance"), secondary_y=True)
fig.update_layout(title_text='<b>TVL vs. Pool Growth</b>')
fig.update_xaxes(title_text='timestep')
fig.update_yaxes(title_text='<b>TVL total_token_value</b> in USD', secondary_y=False)
fig.update_yaxes(title_text='<b>total_token_balance</b> in #', secondary_y=True)
fig.show()  

### C1.1 Pool Invariant & Pool Size Growth

In [16]:
#TVL vs. Pool Size Growth
fig = make_subplots(specs=[[{'secondary_y': True}]])
fig.add_trace(go.Scatter(x=p_df.timestep, y=p_df.invariant, line=dict(color='#f36315'), name="Invariant in #"), secondary_y=False)
fig.add_trace(go.Scatter(x=p_df.timestep,y=p_df.total_token_balances, line=dict(color='#2C1839'), name="total_token_balance"), secondary_y=True)
fig.update_layout(title_text='<b>Invariant vs. Pool Growth</b>')
fig.update_xaxes(title_text='timestep')
fig.update_yaxes(title_text='<b>Invariant</b> in #', secondary_y=False,range=[181000, 189000])
fig.update_yaxes(title_text='<b>total_token_balance</b> in #', secondary_y=True)
fig.show()  

### C1.2 Token Balances

In [17]:
#balance growth % (total observation period)
dai_growth = ((p_df.iloc[-1][['token_dai_balance']])-(p_df.iloc[0][['token_dai_balance']]))*100/(p_df.iloc[0][['token_dai_balance']])
weth_growth = ((p_df.iloc[-1][['token_weth_balance']])-(p_df.iloc[0][['token_weth_balance']]))*100/(p_df.iloc[0][['token_weth_balance']])
growth = list(zip(dai_growth, weth_growth)) 
g_df = pd.DataFrame(growth, columns = ['dai_growth','weth_growth' ]).transpose(copy=True).reset_index()
g_df.columns =['token', 'growth']
print(g_df)
#plot
fig = make_subplots(rows=2, cols=2, subplot_titles=('DAI Growth', 'Balance Growth in %', 'WETH Growth'))
fig.add_trace(go.Scatter(x=p_df.timestep, y=p_df.token_dai_balance, line=dict(color='#4675ed'), name='token_dai_balance'), row=1, col=1)
fig.add_trace(go.Scatter(x=p_df.timestep, y=p_df.token_weth_balance, line=dict(color='#4145ab'), name='token_weth_balance'), row=2, col=1)
fig.add_trace(go.Bar(y=g_df.growth, x=g_df.token, marker_color=['#4675ed','#4145ab']), row=1, col=2)
fig.update_layout(height=600, width=1000, showlegend=False, title_text='<b>Balance Growth</b> in observation period')
fig.show()

         token    growth
0   dai_growth -0.582670
1  weth_growth  2.172523


### C1.3 Sources of Growth 

In [18]:
#Pool Shares
fig = px.line(p_df, x=p_df.timestep,y=p_df.pool_shares)
fig.update_layout(height=300, width=1000, title_text='<b>Pool Shares (BPT)</b>')
fig.update_xaxes(title_text='timestep')
fig.update_yaxes(title_text='<b>pool shares</b> in #', range=[-0.05,102.00])
fig.show()

In [19]:
#Fees
fig = make_subplots(rows=2, cols=1)
fig.add_trace(go.Scatter(x=p_df.timestep, y=p_df.generated_fees_dai, line=dict(color='#4675ed'), name='fees DAI'), row=1, col=1)
fig.add_trace(go.Scatter(x=p_df.timestep, y=p_df.generated_fees_weth, line=dict(color='#4145ab'), name='fees WETH'), row=2, col=1)
fig.update_yaxes(title_text='token amount', secondary_y=False)
fig.update_layout(height=500, width=1000, title_text='<b>Fees Generated</b> per transaction')

In [20]:
# DAI fee events vs. ETH fee events
WETH_fee_events = len(p_df[p_df.generated_fees_weth > 0])
DAI_fee_events = len(p_df[p_df.generated_fees_dai > 0])
values = [DAI_fee_events, WETH_fee_events]
labels = ['DAI fees', 'WETH fees']
fig = go.Figure(data=[go.Pie(labels=labels, values=values)])
fig.update_traces(hoverinfo='label+percent', marker=dict(colors=['#4675ed','#4145ab']))
fig.update_layout(height=500, width=1000, title_text='<b>Fee generating events</b> in total observation time')
fig.show()

In [21]:
#proportions of fee value contribution, in fixed USD value
daif = p_df.groupby('action_type').sum()['generated_fees_dai'].drop(['external_price_update'])
wethf = p_df.groupby('action_type').sum()['generated_fees_weth'].drop(['external_price_update'])
fee_v = pd.concat([daif, wethf], axis=1)

#calculate USD value (define USD value, in this case locked to initial state observation time)
fee_v['DAI_fee_value'] = fee_v.generated_fees_dai*1.0053414509361551 #define DAI price
fee_v['WETH_fee_value'] = fee_v.generated_fees_weth*594.3526451552318 #define WETH price

#add total 
fee_v = fee_v.append(fee_v.sum().rename('total'))
print(fee_v)

#plot pie chart comparing ETH fees vs DAI fees
values = [fee_v.loc['total']['DAI_fee_value'], fee_v.loc['total']['WETH_fee_value']] 
labels = ['DAI_fees', 'WETH_fees']
fig = go.Figure(data=[go.Pie(labels=labels, values=values)])
fig.update_traces(hoverinfo='label+percent', marker=dict(colors=['#4675ed','#4145ab']))
fig.update_layout(height=500, width=1000, title_text="<b>Fee value contribution</b> in USD, in total observation time")
fig.show()

             generated_fees_dai  generated_fees_weth  DAI_fee_value  \
action_type                                                           
total                       0.0                  0.0            0.0   

             WETH_fee_value  
action_type                  
total                   0.0  


In [22]:
# FEE PER DAY/in fixed USD value

#calculate USD value (define USD value, in this case locked to initial state observation time)
fee_t = p_df[['change_datetime']].dropna()
fee_t['DAI_fee_value'] = p_df.generated_fees_dai*1.0053414509361551 #define DAI price
fee_t['WETH_fee_value'] = p_df.generated_fees_weth*594.3526451552318 #define WETH price
daily = fee_t.groupby(pd.Grouper(key='change_datetime',freq='D')).sum() #sum per week

#plot value per week
fig = go.Figure(data=[go.Bar(name='DAI fees', x=daily.index, y=daily.DAI_fee_value, marker_color='#4675ed', offsetgroup=0), go.Bar(name='WETH fees', x=daily.index, y=daily.WETH_fee_value, marker_color='#4145ab', offsetgroup=1)], layout=go.Layout(title='<b>Fees per day</b> in USD', yaxis_title='USD value'))
fig.show()

### C1.4 Token Ratio

In [23]:
events = [0, -1] #Start/End of observation period
ratio = pd.DataFrame(p_df.iloc[events][['token_dai_balance','token_weth_balance']]).transpose(copy=True)
ratio.columns =['start', 'end'] 
#plot
fig = make_subplots(rows=1, cols=2, specs=[[{'type':'domain'}, {'type':'domain'}]])
fig.add_trace(go.Pie(labels=ratio.index, values=ratio.start), 1, 1)
fig.add_trace(go.Pie(labels=ratio.index, values=ratio.end), 1, 2)
fig.update_traces(hoverinfo='label+percent+name', marker=dict(colors=['#4675ed','#4145ab']))
fig.update_layout(height=400, width=1000, title_text='<b>Token Ratio</b> Start/End Observation Period in %')
fig.show()